# Harjoitus 2

TIEA2400
Kevät 2025

Notebookin palautus: joonas.k.hamalainen@jyu.fi
- Nimeä palautettu tiedosto seuraavasti: tiea2400_h2_sukunimi_etunimi.ipynb.
- Laita sähköpostin otsikkokentän alkuun koodi: [TIEA2400]

## Tehtävä 2 (Muuttujatyyppien muunnokset)

Tässä tehtävässä käytetään luennolla esitettyä modifioitua Titanic datajoukkoa.

a) Lataa modifioitu Titanic datajoukko täältä [Titanic](http://users.jyu.fi/~jookriha/TIEA2400/Titanic_Data_Modified/titanic_modified.csv). Tehtävänä on jalostaa tästä datasta muunnettu datajoukko, jota voitaisiin tarvittaessa käyttää koneoppimismallin opetuksessa. Valitse datasta seuraavat muuttujat: 'PassengerId', 'Survived', 'Embarked', 'Pclass', 'Age', 'Sex', 'Comment'. Aloitetaan muokkaamalla kategoriset muuttujat numeerisiksi. Muunna nominaaliset muuttujat ensin one-hot-encoding konvention muokaisesti uusiksi muuttujiksi. Seuraavaksi muunna järjestykselliset muuttujat numeerisiksi.

In [2]:
import pandas as pd
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import LabelBinarizer

# Modifioitu Titanic data tiedosto
url = "http://users.jyu.fi/~jookriha/TIEA2400/Titanic_Data_Modified/titanic_modified.csv"

# Ladataan data csv-tiedostosta
D = pd.read_csv(url)

print(D.head())
print('\n')
print(D.isnull().sum())

   PassengerId Survived     Embarked Pclass   Age     Sex  \
0            1       No  Southampton    3rd  22.0    male   
1            2      Yes    Cherbourg    1st  38.0  female   
2            3      Yes  Southampton    3rd  26.0  female   
3            4      Yes  Southampton    1st  35.0  female   
4            5       No  Southampton    3rd  35.0    male   

                                         Comment  
0     Soup was so thin I saw my reflection in it  
1              Bread was harder than my bunk bed  
2                 Tea so weak it needed rescuing  
3  Stew tasted like the ocean including the salt  
4          Fish was so fresh it almost swam away  


PassengerId     0
Survived        0
Embarked        1
Pclass          0
Age            22
Sex             0
Comment         0
dtype: int64


Age ja Embarked muuttujat sisältävät tyhjiä arvoja -> imputoidaan kukin puuttuva arvo sen muuttujan esiintymistiheydeltään suurimmalla arvolla

In [3]:
from sklearn.impute import SimpleImputer
imputer = SimpleImputer(strategy='most_frequent')
D[['Age']] = imputer.fit_transform(D[['Age']])
D[['Embarked']] = imputer.fit_transform(D[['Embarked']])
print(D.head())
print('\n')
print(D.isnull().sum())

   PassengerId Survived     Embarked Pclass   Age     Sex  \
0            1       No  Southampton    3rd  22.0    male   
1            2      Yes    Cherbourg    1st  38.0  female   
2            3      Yes  Southampton    3rd  26.0  female   
3            4      Yes  Southampton    1st  35.0  female   
4            5       No  Southampton    3rd  35.0    male   

                                         Comment  
0     Soup was so thin I saw my reflection in it  
1              Bread was harder than my bunk bed  
2                 Tea so weak it needed rescuing  
3  Stew tasted like the ocean including the salt  
4          Fish was so fresh it almost swam away  


PassengerId    0
Survived       0
Embarked       0
Pclass         0
Age            0
Sex            0
Comment        0
dtype: int64


Tehdään one-hot-encoding Embarked-muuttujalle ja muunnetaan binääriset muuttujat Sex ja Survived numeerisiksi

In [4]:
one_hot_encoder = OneHotEncoder(sparse_output=False)
muunnettu_data = one_hot_encoder.fit_transform(D[['Embarked']])

muunnetut_muuttujanimet = one_hot_encoder.get_feature_names_out(['Embarked'])
D_muunnettu = pd.DataFrame(muunnettu_data, columns=muunnetut_muuttujanimet)

binarizer = LabelBinarizer()
D_muunnettu['Sex'] = binarizer.fit_transform(D['Sex'])
D_muunnettu['Survived'] = binarizer.fit_transform(D['Survived'])
D_muunnettu.head()

Embarked_Cherbourg  Embarked_Queenstown  Embarked_Southampton  Sex  \
0                 0.0                  0.0                   1.0    1   
1                 1.0                  0.0                   0.0    0   
2                 0.0                  0.0                   1.0    0   
3                 0.0                  0.0                   1.0    0   
4                 0.0                  0.0                   1.0    1   

   Survived  
0         0  
1         1  
2         1  
3         1  
4         0

Muunnetaan järjestyksellinen muuttuja Pclass numeeriseksi

In [5]:
ordinal_encoder = OrdinalEncoder(categories=[['1st','2nd','3rd']])
D_muunnettu[['Pclass']] = ordinal_encoder.fit_transform(D[['Pclass']])
D_muunnettu.head()

Embarked_Cherbourg  Embarked_Queenstown  Embarked_Southampton  Sex  \
0                 0.0                  0.0                   1.0    1   
1                 1.0                  0.0                   0.0    0   
2                 0.0                  0.0                   1.0    0   
3                 0.0                  0.0                   1.0    0   
4                 0.0                  0.0                   1.0    1   

   Survived  Pclass  
0         0     2.0  
1         1     0.0  
2         1     2.0  
3         1     0.0  
4         0     2.0

Lisätään muunnetut muuttujat alkuperäiseen dataan ja poistetaan niitä vastaavat muuntamattomat muuttujat

In [6]:
# Lisätään alkuperäiseen DataFrameen muunnetut
D_muunnettu = pd.concat([D.drop(['Embarked', 'Sex','Survived','Pclass'], axis=1), D_muunnettu], axis=1)
D_muunnettu.head()


PassengerId   Age                                        Comment  \
0            1  22.0     Soup was so thin I saw my reflection in it   
1            2  38.0              Bread was harder than my bunk bed   
2            3  26.0                 Tea so weak it needed rescuing   
3            4  35.0  Stew tasted like the ocean including the salt   
4            5  35.0          Fish was so fresh it almost swam away   

   Embarked_Cherbourg  Embarked_Queenstown  Embarked_Southampton  Sex  \
0                 0.0                  0.0                   1.0    1   
1                 1.0                  0.0                   0.0    0   
2                 0.0                  0.0                   1.0    0   
3                 0.0                  0.0                   1.0    0   
4                 0.0                  0.0                   1.0    1   

   Survived  Pclass  
0         0     2.0  
1         1     0.0  
2         1     2.0  
3         1     0.0  
4         0     2.0


b) Jatka modifioidun Titanic datajoukon muuntamista. Muunnetaan seuraavaksi teksikentän datan (synteettisesti generoitu matkustajien palaute Titanicin ravintolan ruokailusta) luennolla esitellyn Bag-of-Words (BoW) mallin mukaiseen formaattiin. Esikäsittele kommentit poistamalla pysäytyssanat (stop words) ja muunna kaikki kirjaimet pieniksi. Mitkä ovat muodostetun sanaston viisi yleisintä sanaa ja niiden esiintymistiheydet?

In [7]:
from sklearn.feature_extraction.text import CountVectorizer
import nltk
from nltk.corpus import stopwords

nltk.download('stopwords')
pysaytys_sanat = set(stopwords.words('english'))

def poista_pysaytys_sanat(text):
    sanat = text.split()
    suodatetut_sanat = [sana for sana in sanat if sana not in pysaytys_sanat]
    return " ".join(suodatetut_sanat)

D_muunnettu['Comment'] = D_muunnettu['Comment'].str.lower().apply(poista_pysaytys_sanat)

bow_muunnin = CountVectorizer()
D_bow = bow_muunnin.fit_transform(D_muunnettu['Comment'])
D_bow_df = pd.DataFrame(D_bow.toarray(), columns=bow_muunnin.get_feature_names_out())

esiintymistiheys = D_bow.toarray().sum(axis=0)
sanasto_df = pd.DataFrame({'sana': bow_muunnin.get_feature_names_out(), 'esiintymistiheys': esiintymistiheys})

sanasto_sorted_df = sanasto_df.sort_values(by="esiintymistiheys", ascending=False)
print(sanasto_sorted_df.head())


      sana  esiintymistiheys
194   soup                11
217    tea                 8
93    fish                 8
25   bread                 8
55   could                 8


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.



c) Jatka b-kohdan BoW piirteiden muuntamista. Laske lopuksi luennolla (Luento 4) esitetyn TF-IDF mallin mukaiset muunnetut piirteet hyödyntäen BoW-piirteytystä syötteenä. Miten BoW-piirteiden (sanojen) vaikutus muuttuu TF-IDF-piirteytyksessä?

In [8]:
from sklearn.feature_extraction.text import TfidfTransformer
tf_idf = TfidfTransformer()
D_tf_idf = tf_idf.fit_transform(D_bow)
D_tf_idf_df = pd.DataFrame(D_tf_idf.toarray(), columns = bow_muunnin.get_feature_names_out())
D_tf_idf_df.head()

actual  adventure  afterthought  ago  air    almost  ambition  asked  \
0     0.0        0.0           0.0  0.0  0.0  0.000000       0.0    0.0   
1     0.0        0.0           0.0  0.0  0.0  0.000000       0.0    0.0   
2     0.0        0.0           0.0  0.0  0.0  0.000000       0.0    0.0   
3     0.0        0.0           0.0  0.0  0.0  0.000000       0.0    0.0   
4     0.0        0.0           0.0  0.0  0.0  0.479273       0.0    0.0   

   atlantic  avoided  ...  useful  waiter  want  warm  water      weak  \
0       0.0      0.0  ...     0.0     0.0   0.0   0.0    0.0  0.000000   
1       0.0      0.0  ...     0.0     0.0   0.0   0.0    0.0  0.000000   
2       0.0      0.0  ...     0.0     0.0   0.0   0.0    0.0  0.557722   
3       0.0      0.0  ...     0.0     0.0   0.0   0.0    0.0  0.000000   
4       0.0      0.0  ...     0.0     0.0   0.0   0.0    0.0  0.000000   

   weapon  wishful  wood  york  
0     0.0      0.0   0.0   0.0  
1     0.0      0.0   0.0   0.0  
2     0.0      0.0   0.0   0.0  
3     0.0      0.0   0.0   0.0  
4     0.0      0.0   0.0   0.0  

[5 rows x 244 columns]

BoW-piirteytykseen verrattuna TF-IDF-piirteytys vähentää yleisten sanojen painotusta ja lisää harvinaisten sanojen painotusta IDF-termillä.